In [1]:
import Pkg; Pkg.installed()


Dict{String,Union{Nothing, VersionNumber}} with 26 entries:
  "CSV"                   => v"0.5.6"
  "MCMCChains"            => v"0.3.10"
  "StatsModels"           => v"0.5.0"
  "DataStreams"           => v"0.4.2"
  "Distributions"         => v"0.20.0"
  "Random"                => nothing
  "Atom"                  => v"0.8.7"
  "Suppressor"            => v"0.1.1"
  "StatsPlots"            => v"0.11.0"
  "Juno"                  => v"0.7.0"
  "Query"                 => v"0.11.0"
  "StatisticalRethinking" => v"0.8.5"
  "StatsBase"             => v"0.30.0"
  "AxisArrays"            => v"0.3.0"
  "IJulia"                => v"1.18.1"
  "RDatasets"             => v"0.6.2"
  "CategoricalArrays"     => v"0.5.4"
  "RData"                 => v"0.6.0"
  "Gadfly"                => v"1.0.1"
  "StatsFuns"             => v"0.8.0"
  "JLD2"                  => v"0.1.2"
  "MLLabelUtils"          => v"0.5.1"
  "Cairo"                 => v"0.6.0"
  "RCall"                 => v"0.13.3"
  "DataFrames"        

In [426]:
## set working directory
cd("/Users/nhungnguyen/Documents/courses/Books and Papers/Julia")

## using these packages, if not available => use Pkg.add() to download
using Turing, CSV, Query, MCMCChains, DataFrames, StatsBase, Distributions, JLD2, CategoricalArrays, StatsPlots, StatsFuns, RData,
DynamicHMC, Distributed

In [65]:
############# Statistical Rethinking - Milk model (m5.7), linear regression of Kcal on neocortex and mass

## import data
milk = CSV.read("milk.csv",
    missingstrings = ["nan", "NA", "na", ""])

## keep non-missing data
milk_nm = dropmissing(milk)

## function to scale variables
function center(y)
    return((y .- mean(y)) ./ std(y))
    end

## Scale KCalories, Neo and Mass
K = center(milk_nm[:kcal_per_g])
N = center(milk_nm[:neocortex_perc])
M = center(log.(milk_nm[:mass]))

# define model
@model milk5_7(K, N, M) = begin
    
    #prior for sigma
    sigma ~ Exponential(1)
    
    # prior for bM
    bM ~ Normal(0, 0.5)
    
    # prior for bN
    bN ~ Normal(0, 0.5)
    
    # prior for intercept
    a ~ Normal(0, 0.2)
    
    #likelihood
    n_obs = length(K)
    mu = a .+ bN .* N .+ bM .* M
    
    for i in 1:n_obs
        K[i] ~ Normal(mu[i], sigma)
    end
    end;

iterations = 4000
ϵ = 0.05
τ = 10

# start sampling
chain_milk = sample(milk5_7(K, N, M), HMC(iterations, ϵ, τ))

p = MCMCChains.plot(chain_milk)


LoadError: syntax: invalid identifier name "."

In [64]:
############# Statistical Rethinking - Milk model (m5.10), with categorical variables: clade and house
milk = CSV.read("milk.csv",
    missingstrings = ["nan", "NA", "na", ""])

K = center(milk[:kcal_per_g])

clade = milk[:clade]
clade_id = recode(clade, "Strepsirrhine" => 4, "Ape" => 1, "New World Monkey" => 2, "Old World Monkey" => 3)

house_id = sample(repeat([1,2, 3, 4],8), length(K))

# define model
@model milk5_10(K, clade_id, house_id) = begin
    
    #prior for sigma
    sigma ~ Exponential(1)
    
    
    # prior for h
    h = Array{Real}(undef, 4)
    h ~ [Normal(0, 0.5)]
    
    
    # prior for a
    a = Array{Real}(undef, 4)
    a ~ [Normal(0, 0.5)]
    
    
    #likelihood
    n_obs = length(K)
    mu = a[clade_id] + h[house_id]
    
    for i in 1:n_obs
        K[i] ~ Normal(mu[i], sigma)
    end
    end;

iterations = 20000
ϵ = 0.01
τ = 5

# start sampling
chain_milk_10 = sample(milk5_10(K, clade_id, house_id), HMC(iterations, ϵ, τ))

# trace plot
p = MCMCChains.plot(chain_milk_10)

## multiple chains
num_chains = 4
chains_4 = mapreduce(c -> sample(milk5_10(K, clade_id, house_id), HMC(iterations, ϵ, τ)), chainscat, 1:num_chains)

## Gelman Diagnostic
gelmandiag(chains_4)

## NUTS samples instead of HMC sampler
chain_milk_10_NUTS = sample(milk5_10(K, clade_id, house_id), NUTS(iterations, 0.65))

[HMC] Sampling...  0%  ETA: 14:30:07
  ϵ:         0.1
  α:         1.0
4m  pre_cond:  [1.0]


[HMC] Sampling...  3%  ETA: 0:02:03
  ϵ:         0.1
  α:         0.8250441988176892
4m  pre_cond:  [1.0]


[HMC] Sampling...  6%  ETA: 0:01:17
  ϵ:         0.1
  α:         1.0
4m  pre_cond:  [1.0]


[HMC] Sampling...  9%  ETA: 0:01:02
  ϵ:         0.1
  α:         1.0
4m  pre_cond:  [1.0]


[HMC] Sampling... 11%  ETA: 0:00:53
  ϵ:         0.1
  α:         1.0
4m  pre_cond:  [1.0]


[HMC] Sampling... 14%  ETA: 0:00:47
  ϵ:         0.1
  α:         1.0
4m  pre_cond:  [1.0]


[HMC] Sampling... 17%  ETA: 0:00:43
  ϵ:         0.1
  α:         1.0
4m  pre_cond:  [1.0]


[HMC] Sampling... 20%  ETA: 0:00:39
  ϵ:         0.1
  α:         0.9310162189311622
4m  pre_cond:  [1.0]


[HMC] Sampling... 23%  ETA: 0:00:37
  ϵ:         0.1
  α:         0.9245440223061381
4m  pre_cond:  [1.0]


[HMC] Sampling... 26%  ETA: 0:00:34
  ϵ:         0.1
  α:         0.792391890411847
4m  pre_cond:  [1.0]


[HMC] Samp

[HMC] Finished with
  Running time        = 38.294768233000056;
  Accept rate         = 0.93545;
  #lf / sample        = 4.99975;
  #evals / sample     = 5.0e-5;
  pre-cond. metric    = [1.0].


In [3]:
############# Statistical Rethinking - Rugged model (m8.5), linear regression of log_gdp on rugged, 
############## for african and non-african countries

## import data
rugged = CSV.read("rugged.csv",
    missingstrings = ["nan", "NA", "na", ""])

## keep non-missing data
rugged_nm = dropmissing(rugged[:, [:rgdppc_2000, :rugged, :cont_africa]])

rugged_nm[:log_gdp] = log.(rugged_nm[:rgdppc_2000])

## rescale log_gdp and rugged
log_gdp_std = rugged_nm[:log_gdp] ./ mean(rugged_nm[:log_gdp])
rugged_std = rugged_nm[:rugged] ./ maximum(rugged_nm[:rugged]) 
africa_id = rugged_nm[:cont_africa] .+ 1


# define model
@model rugged_model(log_gdp, rugged, africa_id) = begin
    
    #prior for sigma
    sigma = Array{Float64}(undef, 1)
    sigma ~ Exponential(1)
    
    # prior for b
    b = Array{Float64}(undef, 2)
    b ~ [Normal(0, 0.3)]
    
    # prior for a
    a = Array{Float64}(undef, 2)
    a ~ [Normal(1, 0.1)]
    
    
    #likelihood
    n_obs = length(log_gdp)
    mu = a[africa_id] .+ b[africa_id] .* (rugged .- 0.215)
    
    for i in 1:n_obs
        log_gdp[i] ~ Normal(mu[i], sigma)
    end
    end;

iterations = 4000
ϵ = 0.05
τ = 10

# start sampling, HMC sampler
#chain_rugged = sample(rugged_model(log_gdp_std, rugged_std, africa_id), HMC(iterations, ϵ, τ))

## NUTS samples
chain_rugged_NUTS = sample(rugged_model(log_gdp_std, rugged_std, africa_id), NUTS(iterations, 0.65))

# trace plot
p = MCMCChains.plot(chain_rugged_NUTS)

┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.15361328125
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
[NUTS] Sampling...  0%  ETA: 0:19:41
  ϵ:         0.008923026079469988
  α:         0.9982634517714795
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  2%  ETA: 0:04:03
  ϵ:         0.016871589209204847
  α:         0.8546569760537489
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  4%  ETA: 0:02:45
  ϵ:         0.00866941814202532
  α:         0.96114859084462
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  5%  ETA: 0:02:09
  ϵ:         0.017850185928171933
  α:         0.9495241370394389
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  7%  ETA: 0:01:51
  ϵ:         0.004261577535777577
  α:         0.9835854401525084
4m  p

InterruptException: InterruptException:

In [91]:
############# Statistical Rethinking - Tulips model (m8.7), linear regression of bloom on water, shade and water*shade 

## import data
tulips= CSV.read("tulips.csv",
    missingstrings = ["nan", "NA", "na", ""])


## rescale variables
blooms_std = tulips[:blooms] ./ maximum(tulips[:blooms])
water_cent = tulips[:water] .- mean(tulips[:water])
shade_cent = tulips[:shade] .- mean(tulips[:shade])


# define model
@model tulips_model(blooms, water, shade) = begin
    
    #prior for sigma
    sigma ~ Exponential(1)
    
    # prior for bws
    bws ~ Normal(0, 0.25)
    
    # prior for bs
    bs ~ Normal(0, 0.25)
    
    # prior for bw
    bw ~ Normal(0, 0.25)
    
    # prior for a
    a ~ Normal(0.5, 0.25)
    
    
    #likelihood
    n_obs = length(blooms)
    mu = a .+ bw .* water .+ bs .* shade .+ bws .* water .* shade
    
    for i in 1:n_obs
        blooms[i] ~ Normal(mu[i], sigma)
    end
    end;

iterations = 10000
ϵ = 0.05
τ = 10

# start sampling, HMC sampler
#chain_tulips = sample(tulips_model(blooms_std, water_cent, shade_cent), HMC(iterations, ϵ, τ))

## NUTS samples
chain_tulips_NUTS = sample(tulips_model(blooms_std, water_cent, shade_cent), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_tulips_NUTS)

┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.45078125
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
[NUTS] Sampling...  1%  ETA: 0:03:59
  ϵ:         0.026265458652124797
  α:         0.8126362389995946
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  3%  ETA: 0:02:34
  ϵ:         0.12008898907418789
  α:         1.2097280016144508e-62
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  4%  ETA: 0:01:55
  ϵ:         0.043022418090198564
  α:         0.6428980977538918
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  6%  ETA: 0:01:33
  ϵ:         0.03768881189510912
  α:         0.9187399974066405
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling...  7%  ETA: 0:01:27
  ϵ:         0.030797669406254894
  α:         0.966473677301368
4m  

[NUTS] Finished with
  Running time        = 84.49390639500008;
  #lf / sample        = 0.0;
  #evals / sample     = 0.0001;
  pre-cond. metric    = [1.0, 1.0, 1.0, 1.0, 1.0].


Object of type Chains, with data of type 10000×11×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:10000
Thinning interval = 1
Chains            = 1
Samples per chain = 10000
internals         = elapsed, epsilon, eval_num, lf_eps, lf_num, lp
parameters        = sigma, bw, bws, a, bs

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 2 columns
│ Row │ parameters │ mean      │ std       │ naive_se    │ mcse        │
│     │ Symbol     │ Float64   │ Float64   │ Float64     │ Float64     │
├─────┼────────────┼───────────┼───────────┼─────────────┼─────────────┤
│ 1   │ a          │ 0.35817   │ 0.0331412 │ 0.000331412 │ 0.0002521   │
│ 2   │ bs         │ -0.113026 │ 0.0550196 │ 0.000550196 │ 0.00031654  │
│ 3   │ bw         │ 0.205165  │ 0.0436488 │ 0.000436488 │ 0.000534844 │
│ 4   │ bws        │ -0.142208 │ 0.055526  │ 0.00055526  │ 0.000448008 │
│ 5   │ sigma      │ 0.146001  │ 0.158492  │ 0.00158492  │ 0.00361871  │

Quantiles
.

In [97]:
############# Statistical Rethinking - Chimpanzees model (m11.3)
## import data
chimpanzees= CSV.read("chimpanzees.csv",
    missingstrings = ["nan", "NA", "na", ""])

pulled_left = chimpanzees[:pulled_left]
condition = chimpanzees[:condition]
prosoc_left = chimpanzees[:prosoc_left]

# define model
@model chimp_model(pull, cond, pros) = begin
    
    # prior for bpC
    bpC ~ Normal(0, 10)
    
    # prior for bp
    bp ~ Normal(0, 10)
    
    # prior for a
    a ~ Normal(0, 10)
    
    
    #likelihood
    n_obs = length(pull)
    logit_p = a .+ (bp .* pros) .+ (bpC .* cond .* pros)
    
    for i in 1:n_obs
        pull[i] ~ BinomialLogit(1, logit_p[i])
    end
    end;

iterations = 10000
ϵ = 0.05
τ = 10

# start sampling, HMC sampler
#chain_chimp = sample(chimp_model(pulled_left, condition, prosoc_left), HMC(iterations, ϵ, τ))

## NUTS samples
chain_chimp_NUTS = sample(chimp_model(pulled_left, condition, prosoc_left), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_chimp_NUTS)




┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.2150390625
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
[NUTS] Sampling...  0%  ETA: 0:57:46m
  ϵ:         0.019818736547429036
  α:         0.999484493833434
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling...  0%  ETA: 0:34:31
  ϵ:         0.0360761363710127
  α:         0.9981966422920017
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling...  0%  ETA: 0:27:24
  ϵ:         0.041621531218850163
  α:         0.9992013747778893
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling...  1%  ETA: 0:22:32
  ϵ:         0.15109527836210002
  α:         0.9566112863657947
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling...  1%  ETA: 0:19:45
  ϵ:         0.13502849900449285
  α:         0.6774159010875102
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Samplin

4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 22%  ETA: 0:05:55
  ϵ:         0.14211216065360482
  α:         0.6963548881379282
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 23%  ETA: 0:05:53
  ϵ:         0.14211216065360482
  α:         0.8302524056085266
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 23%  ETA: 0:05:52
  ϵ:         0.14211216065360482
  α:         0.9860169203655113
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 23%  ETA: 0:05:49
  ϵ:         0.14211216065360482
  α:         0.5190753086436539
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 23%  ETA: 0:05:47
  ϵ:         0.14211216065360482
  α:         0.8074266101044885
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 24%  ETA: 0:05:45
  ϵ:         0.14211216065360482
  α:         0.5832506008418039
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 24%  ETA: 0:05:43
  ϵ:         0.14211216065360482
  α:         0.9882009470685333
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 24%

4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 36%  ETA: 0:04:33
  ϵ:         0.14211216065360482
  α:         0.6933043917888657
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 36%  ETA: 0:04:32
  ϵ:         0.14211216065360482
  α:         0.45064759516025826
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 36%  ETA: 0:04:30
  ϵ:         0.14211216065360482
  α:         0.005984470926111582
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 36%  ETA: 0:04:29
  ϵ:         0.14211216065360482
  α:         0.9139263235355637
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 37%  ETA: 0:04:28
  ϵ:         0.14211216065360482
  α:         0.5260227152843386
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 37%  ETA: 0:04:27
  ϵ:         0.14211216065360482
  α:         0.9980774991218475
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 37%  ETA: 0:04:26
  ϵ:         0.14211216065360482
  α:         0.4923855547474873
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 

4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 50%  ETA: 0:03:24
  ϵ:         0.14211216065360482
  α:         0.5393223366218495
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 50%  ETA: 0:03:22
  ϵ:         0.14211216065360482
  α:         0.9228642758513967
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 50%  ETA: 0:03:21
  ϵ:         0.14211216065360482
  α:         0.8427423593755909
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 50%  ETA: 0:03:20
  ϵ:         0.14211216065360482
  α:         0.7197471669315503
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 51%  ETA: 0:03:18
  ϵ:         0.14211216065360482
  α:         0.9984590504019393
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 51%  ETA: 0:03:17
  ϵ:         0.14211216065360482
  α:         0.6080788129312371
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 51%  ETA: 0:03:15
  ϵ:         0.14211216065360482
  α:         0.07047256388833802
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 52

4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 65%  ETA: 0:02:17
  ϵ:         0.14211216065360482
  α:         0.6502026942181123
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 65%  ETA: 0:02:15
  ϵ:         0.14211216065360482
  α:         0.935813443865997
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 65%  ETA: 0:02:14
  ϵ:         0.14211216065360482
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 66%  ETA: 0:02:13
  ϵ:         0.14211216065360482
  α:         0.937870342748487
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 66%  ETA: 0:02:12
  ϵ:         0.14211216065360482
  α:         0.8644771271169281
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 66%  ETA: 0:02:10
  ϵ:         0.14211216065360482
  α:         0.9474434323640134
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 67%  ETA: 0:02:09
  ϵ:         0.14211216065360482
  α:         0.7005430802177137
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 67%  ETA: 0:02:08
  

4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 79%  ETA: 0:01:18
  ϵ:         0.14211216065360482
  α:         0.09260828508660207
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 80%  ETA: 0:01:16
  ϵ:         0.14211216065360482
  α:         5.859798559428393e-5
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 80%  ETA: 0:01:15
  ϵ:         0.14211216065360482
  α:         0.8296135667950136
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 80%  ETA: 0:01:14
  ϵ:         0.14211216065360482
  α:         0.8321607531392403
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 81%  ETA: 0:01:13
  ϵ:         0.14211216065360482
  α:         0.31188032339397165
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 81%  ETA: 0:01:11
  ϵ:         0.14211216065360482
  α:         0.8617577795498179
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 81%  ETA: 0:01:10
  ϵ:         0.14211216065360482
  α:         0.48510781354882915
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling..

4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 94%  ETA: 0:00:21
  ϵ:         0.14211216065360482
  α:         0.07876461591853745
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 95%  ETA: 0:00:20
  ϵ:         0.14211216065360482
  α:         0.6279889027498916
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 95%  ETA: 0:00:19
  ϵ:         0.14211216065360482
  α:         0.9503711768209498
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 95%  ETA: 0:00:17
  ϵ:         0.14211216065360482
  α:         0.4018269236126156
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 96%  ETA: 0:00:16
  ϵ:         0.14211216065360482
  α:         0.653115052043913
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 96%  ETA: 0:00:15
  ϵ:         0.14211216065360482
  α:         0.7376527947508527
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 96%  ETA: 0:00:14
  ϵ:         0.14211216065360482
  α:         0.9091098942344362
4m  pre_cond:  [1.0, 1.0, 1.0]


[NUTS] Sampling... 97%

[NUTS] Finished with
  Running time        = 366.0476889079995;
  #lf / sample        = 0.0;
  #evals / sample     = 0.0001;
  pre-cond. metric    = [1.0, 1.0, 1.0].


Object of type Chains, with data of type 10000×9×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:10000
Thinning interval = 1
Chains            = 1
Samples per chain = 10000
internals         = elapsed, epsilon, eval_num, lf_eps, lf_num, lp
parameters        = bp, a, bpC

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean      │ std      │ naive_se   │ mcse       │ ess     │
│     │ Symbol     │ Float64   │ Float64  │ Float64    │ Float64    │ Any     │
├─────┼────────────┼───────────┼──────────┼────────────┼────────────┼─────────┤
│ 1   │ a          │ 0.0470348 │ 0.132898 │ 0.00132898 │ 0.00184907 │ 592.307 │
│ 2   │ bp         │ 0.618364  │ 0.230176 │ 0.00230176 │ 0.00404481 │ 3031.58 │
│ 3   │ bpC        │ -0.10946  │ 0.270371 │ 0.00270371 │ 0.0058259  │ 1071.13 │

Quantiles

│ Row │ parameters │ 2.5%      │ 25.0%      │ 50.0%     │ 75.0%    │ 97.5%    │
│     │ Symbol     │ Float64   │ Flo

In [100]:
############# Statistical Rethinking - Chapter 11 - Chimpanzees model (m11.4), each intercept for each actor (7 actors)
## import data
chimpanzees= CSV.read("chimpanzees.csv",
    missingstrings = ["nan", "NA", "na", ""])

pulled_left = chimpanzees[:pulled_left]
condition = chimpanzees[:condition]
prosoc_left = chimpanzees[:prosoc_left]
actor = chimpanzees[:actor]
n_actor = length(unique(actor))

# define model
@model chimp_model_2(pull, cond, pros, actor) = begin
    
    # prior for bpC
    bpC ~ Normal(0, 10)
    
    # prior for bp
    bp ~ Normal(0, 10)
    
    # prior for as, 7 a
    a = Array{Real}(undef, n_actor)
    a ~ [Normal(0, 10)]
    
    
    #likelihood
    n_obs = length(pull)
    logit_p = a[actor] .+ (bp .* pros) .+ (bpC .* cond .* pros)
    
    for i in 1:n_obs
        pull[i] ~ BinomialLogit(1, logit_p[i])
    end
    end;

iterations = 10000
ϵ = 0.05
τ = 10

# start sampling, HMC sampler
#chain_chimp = sample(chimp_model(pulled_left, condition, prosoc_left), HMC(iterations, ϵ, τ))

## NUTS samples
chain_chimp_2_NUTS = sample(chimp_model_2(pulled_left, condition, prosoc_left, actor), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_chimp_NUTS)

┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.34140625
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
[NUTS] Sampling...  0%  ETA: 0:44:03
  ϵ:         0.08008289109119314
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  0%  ETA: 0:36:47
  ϵ:         0.04352937320482035
  α:         0.9938743005457218
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  0%  ETA: 0:37:44
  ϵ:         0.11323901362607712
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  0%  ETA: 0:35:19
  ϵ:         0.05078073640889952
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  0%  ETA: 0:36:14
  ϵ:         0.24248262680411656
  α:         0.1067361368545581
4m  pre_cond:  [1.0, 1.

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:30:39
  ϵ:         0.1215460939358711
  α:         0.8360182771097096
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:31:09
  ϵ:         0.20579793192897444
  α:         0.8550155477467245
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:31:24
  ϵ:         0.1138196437062526
  α:         0.9985146097856852
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:31:27
  ϵ:         0.06670047659971617
  α:         0.9536428317453236
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:31:21
  ϵ:         0.3478663249473325
  α:         0.004329406322898546
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:31:25
  ϵ:         0.11166693111812331
  α:         0.972604424642537
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  3%  ETA: 0:31

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  9%  ETA: 0:25:09
  ϵ:         0.22170952268719482
  α:         0.44123166987412255
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  9%  ETA: 0:25:03
  ϵ:         0.1329706554859975
  α:         0.9146678307779688
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  9%  ETA: 0:24:59
  ϵ:         0.18359655026714244
  α:         0.8799793512491467
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  9%  ETA: 0:24:58
  ϵ:         0.1509463048410891
  α:         0.980162778429922
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 10%  ETA: 0:24:46
  ϵ:         0.05174205639816194
  α:         0.9900918176222315
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 10%  ETA: 0:24:47
  ϵ:         0.04494488872468122
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 10%  ETA: 0:24:48
  ϵ:       

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 11%  ETA: 0:26:09
  ϵ:         0.07182123952724896
  α:         0.9527552749596854
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 12%  ETA: 0:26:07
  ϵ:         0.07182123952724896
  α:         0.9981028869638465
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 12%  ETA: 0:26:10
  ϵ:         0.07182123952724896
  α:         0.9934545140310471
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 12%  ETA: 0:26:13
  ϵ:         0.07182123952724896
  α:         0.9963415473336988
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 12%  ETA: 0:26:17
  ϵ:         0.07182123952724896
  α:         0.9970163178036389
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 12%  ETA: 0:26:20
  ϵ:         0.07182123952724896
  α:         0.9818406243807846
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 12%  ETA: 0:

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:10
  ϵ:         0.07182123952724896
  α:         0.9788284285816471
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:13
  ϵ:         0.07182123952724896
  α:         0.9943103643214074
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:14
  ϵ:         0.07182123952724896
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:17
  ϵ:         0.07182123952724896
  α:         0.97220174107821
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:16
  ϵ:         0.07182123952724896
  α:         0.9994243570586646
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:17
  ϵ:         0.07182123952724896
  α:         0.9857382688855291
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 15%  ETA: 0:29:20
  ϵ:       

...

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 91%  ETA: 0:03:46
  ϵ:         0.07182123952724896
  α:         0.9999348227740781
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 91%  ETA: 0:03:45
  ϵ:         0.07182123952724896
  α:         0.9487556151849219
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 91%  ETA: 0:03:44
  ϵ:         0.07182123952724896
  α:         0.974717914357624
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 91%  ETA: 0:03:43
  ϵ:         0.07182123952724896
  α:         0.9883634809729226
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 91%  ETA: 0:03:42
  ϵ:         0.07182123952724896
  α:         0.9924860151345438
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 91%  ETA: 0:03:41
  ϵ:         0.07182123952724896
  α:         0.9370882875307417
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 92%  ETA: 0:0

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:03:00
  ϵ:         0.07182123952724896
  α:         0.9944039902966754
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:02:59
  ϵ:         0.07182123952724896
  α:         0.9881984908694574
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:02:57
  ϵ:         0.07182123952724896
  α:         0.9158721205372833
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:02:56
  ϵ:         0.07182123952724896
  α:         0.9465017426906384
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:02:55
  ϵ:         0.07182123952724896
  α:         0.9391096505345862
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:02:54
  ϵ:         0.07182123952724896
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 93%  ETA: 0:02:53
  ϵ:     

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:01:37
  ϵ:         0.07182123952724896
  α:         0.9970233235235471
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:01:36
  ϵ:         0.07182123952724896
  α:         0.9800145238189335
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:01:35
  ϵ:         0.07182123952724896
  α:         0.9885971696709609
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:01:34
  ϵ:         0.07182123952724896
  α:         0.9998896662119834
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:01:33
  ϵ:         0.07182123952724896
  α:         0.9873865846180463
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:01:33
  ϵ:         0.07182123952724896
  α:         0.9941345983405279
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 96%  ETA: 0:

[NUTS] Finished with
  Running time        = 2634.773067662993;
  #lf / sample        = 0.0;
  #evals / sample     = 0.0001;
  pre-cond. metric    = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,....


Object of type Chains, with data of type 10000×15×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:10000
Thinning interval = 1
Chains            = 1
Samples per chain = 10000
internals         = elapsed, epsilon, eval_num, lf_eps, lf_num, lp
parameters        = a[3], a[4], a[6], a[5], a[7], bp, bpC, a[1], a[2]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean      │ std      │ naive_se   │ mcse       │ ess     │
│     │ Symbol     │ Float64   │ Float64  │ Float64    │ Float64    │ Any     │
├─────┼────────────┼───────────┼──────────┼────────────┼────────────┼─────────┤
│ 1   │ a[1]       │ -0.737669 │ 0.273867 │ 0.00273867 │ 0.00234845 │ 10000.0 │
│ 2   │ a[2]       │ 11.4696   │ 5.81934  │ 0.0581934  │ 0.394712   │ 170.829 │
│ 3   │ a[3]       │ -1.04838  │ 0.285897 │ 0.00285897 │ 0.00253805 │ 1574.98 │
│ 4   │ a[4]       │ -1.04737  │ 0.283466 │ 0.00283466 │ 0.00255077 │ 10000.0 │
│ 5   │ 

In [129]:
############# Statistical Rethinking - Chapter 11 - UCBadmit model (m11.9), each intercept for each department
## import data
UCBadmit= CSV.read("UCBadmit.csv",
    missingstrings = ["nan", "NA", "na", ""])

n_obs = size(UCBadmit)[1]

n_dept = length(unique(UCBadmit[:dept]))

admit = UCBadmit[:admit]

applications = UCBadmit[:applications]

male_id = [UCBadmit[:gender][i] == "male" ? 1 : 0 for i = 1:n_obs]

dept_id = recode(UCBadmit[:dept], "A" => 1, "B" => 2, "C" => 3, "D" => 4, "E" => 5, "F" => 6)

# define model
@model admit_model(admit, applications, male, dept) = begin
    
    # prior for bm
    bm ~ Normal(0, 10)
    
    # prior for as, 6 a
    a = Array{Real}(undef, n_dept)
    a ~ [Normal(0, 10)]
    
    
    #likelihood
    logit_p = a[dept] .+ (bm .* male) 
    
    for i in 1:n_obs
        admit[i] ~ BinomialLogit(applications[i], logit_p[i])
    end
    end;

iterations = 10000
ϵ = 0.05
τ = 10

# start sampling, HMC sampler
#chain_admit = sample(admit_model(admit, applications, male_id, dept_id), HMC(iterations, ϵ, τ))

## NUTS samples
chain_admit_NUTS = sample(admit_model(admit, applications, male_id, dept_id), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_admit_NUTS)

┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.09105224609375001
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
[NUTS] Sampling...  1%  ETA: 0:23:33m
  ϵ:         0.022492904104762054
  α:         0.9906578376806926
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  2%  ETA: 0:07:34
  ϵ:         0.01856189037878669
  α:         0.9795275578395775
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  4%  ETA: 0:04:31
  ϵ:         0.03330884031150774
  α:         0.9480882864660972
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  5%  ETA: 0:03:17
  ϵ:         0.06954449732853037
  α:         0.9179534268307623
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...  8%  ETA: 0:02:19
  ϵ:         0.07133840346731017

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 97%  ETA: 0:00:01
  ϵ:         0.061530286084869344
  α:         0.8613775865508349
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling... 99%  ETA: 0:00:00
  ϵ:         0.061530286084869344
  α:         0.6710835421869777
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,...


[NUTS] Sampling...100% Time: 0:00:52


[NUTS] Finished with
  Running time        = 51.51967208000012;
  #lf / sample        = 0.0;
  #evals / sample     = 0.0001;
  pre-cond. metric    = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,....


Object of type Chains, with data of type 10000×13×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:10000
Thinning interval = 1
Chains            = 1
Samples per chain = 10000
internals         = elapsed, epsilon, eval_num, lf_eps, lf_num, lp
parameters        = a[3], a[4], bm, a[5], a[6], a[2], a[1]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 2 columns
│ Row │ parameters │ mean       │ std       │ naive_se    │ mcse        │
│     │ Symbol     │ Float64    │ Float64   │ Float64     │ Float64     │
├─────┼────────────┼────────────┼───────────┼─────────────┼─────────────┤
│ 1   │ a[1]       │ 0.683677   │ 0.108394  │ 0.00108394  │ 0.00148955  │
│ 2   │ a[2]       │ 0.63965    │ 0.120809  │ 0.00120809  │ 0.00162531  │
│ 3   │ a[3]       │ -0.581906  │ 0.0777763 │ 0.000777763 │ 0.000838446 │
│ 4   │ a[4]       │ -0.612915  │ 0.0885189 │ 0.000885189 │ 0.00107484  │
│ 5   │ a[5]       │ -1.0598    │ 0.10595   │ 0.0010595   │ 0

In [131]:
############# Statistical Rethinking - Chapter 11 - Kline model (m11.10),
## import data
Kline= CSV.read("Kline.csv",
    missingstrings = ["nan", "NA", "na", ""])

n_obs = size(Kline)[1]

log_pop = log.(Kline[:population])
contact = [Kline[:contact][i] == "high" ? 1 : 0 for i = 1:n_obs]
total_tools = Kline[:total_tools]


# define model
@model tool_model(total_tools, log_pop, contact) = begin
    
    # prior for bpC
    bPC ~ Normal(0, 1)
    
    # prior for bC
    bC ~ Normal(0, 1)
    
    # prior for bP
    bP ~ Normal(0, 1)
    
    # prior for a
    a ~ Normal(0, 100)
    
    
    #likelihood
    log_lambda = a .+ (bP .* log_pop) .+ (bC .* contact) .+ (bPC .* contact .* log_pop)
    lambda = exp.(log_lambda)
    
    for i in 1:n_obs
        total_tools[i] ~ Poisson(lambda[i])
    end
    end;

iterations = 10000
ϵ = 0.05
τ = 10

# start sampling, HMC sampler
#chain_tool = sample(tool_model(total_tools, log_pop, contact), HMC(iterations, ϵ, τ))

## NUTS samples
chain_tool_NUTS = sample(tool_model(total_tools, log_pop, contact), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_admit_NUTS)

┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ In

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 40%  ETA: 0:02:13
  ϵ:         0.0025444034995991023
  α:         0.9996634673161062
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 40%  ETA: 0:02:13
  ϵ:         0.0025444034995991023
  α:         0.9811808055430598
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 41%  ETA: 0:02:12
  ϵ:         0.0025444034995991023
  α:         0.9987638038241903
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 41%  ETA: 0:02:12
  ϵ:         0.0025444034995991023
  α:         0.9725119402664111
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 41%  ETA: 0:02:11
  ϵ:         0.0025444034995991023
  α:         0.9874778194911396
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 42%  ETA: 0:02:09
  ϵ:         0.0025444034995991023
  α:         0.9063846072514419
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 42%  ETA: 0:02:09
  ϵ:         0.0025444034995991023
  α:         0.9792702504799444
4m  pr

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 53%  ETA: 0:02:00
  ϵ:         0.0025444034995991023
  α:         0.9994699004611498
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 53%  ETA: 0:02:00
  ϵ:         0.0025444034995991023
  α:         0.9878693623565836
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 54%  ETA: 0:02:00
  ϵ:         0.0025444034995991023
  α:         0.9999622038257809
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 54%  ETA: 0:02:00
  ϵ:         0.0025444034995991023
  α:         0.9904027442087342
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 54%  ETA: 0:01:59
  ϵ:         0.0025444034995991023
  α:         0.997790815669784
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 54%  ETA: 0:01:59
  ϵ:         0.0025444034995991023
  α:         0.9913725965325273
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 55%  ETA: 0:01:58
  ϵ:         0.0025444034995991023
  α:         0.9791406892427659
4m  pre

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 67%  ETA: 0:01:34
  ϵ:         0.0025444034995991023
  α:         0.9999163970767183
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 67%  ETA: 0:01:33
  ϵ:         0.0025444034995991023
  α:         1.0
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 67%  ETA: 0:01:32
  ϵ:         0.0025444034995991023
  α:         0.999464503673605
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 68%  ETA: 0:01:31
  ϵ:         0.0025444034995991023
  α:         0.9896181271550759
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 68%  ETA: 0:01:30
  ϵ:         0.0025444034995991023
  α:         0.9951090400779957
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 68%  ETA: 0:01:29
  ϵ:         0.0025444034995991023
  α:         0.9993306633580249
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 69%  ETA: 0:01:28
  ϵ:         0.0025444034995991023
  α:         0.9859613012826504
4m  pre_cond:  [1.0, 1

4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 85%  ETA: 0:00:42
  ϵ:         0.0025444034995991023
  α:         0.9936232552132747
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 85%  ETA: 0:00:41
  ϵ:         0.0025444034995991023
  α:         0.9417916803986712
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 85%  ETA: 0:00:40
  ϵ:         0.0025444034995991023
  α:         0.9997874866338408
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 86%  ETA: 0:00:40
  ϵ:         0.0025444034995991023
  α:         0.9993256125482206
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 86%  ETA: 0:00:39
  ϵ:         0.0025444034995991023
  α:         0.9926972396702496
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 86%  ETA: 0:00:39
  ϵ:         0.0025444034995991023
  α:         0.9983780292996925
4m  pre_cond:  [1.0, 1.0, 1.0, 1.0]


[NUTS] Sampling... 86%  ETA: 0:00:39
  ϵ:         0.0025444034995991023
  α:         0.8693184988951491
4m  pr

[NUTS] Finished with
  Running time        = 272.1326777290001;
  #lf / sample        = 0.0;
  #evals / sample     = 0.0001;
  pre-cond. metric    = [1.0, 1.0, 1.0, 1.0].


Object of type Chains, with data of type 10000×10×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:10000
Thinning interval = 1
Chains            = 1
Samples per chain = 10000
internals         = elapsed, epsilon, eval_num, lf_eps, lf_num, lp
parameters        = bC, bPC, a, bP

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 2 columns
│ Row │ parameters │ mean       │ std       │ naive_se    │ mcse       │
│     │ Symbol     │ Float64    │ Float64   │ Float64     │ Float64    │
├─────┼────────────┼────────────┼───────────┼─────────────┼────────────┤
│ 1   │ a          │ 0.954633   │ 0.345599  │ 0.00345599  │ 0.0224002  │
│ 2   │ bC         │ -0.0589529 │ 0.891388  │ 0.00891388  │ 0.0822279  │
│ 3   │ bP         │ 0.26273    │ 0.0351928 │ 0.000351928 │ 0.00214796 │
│ 4   │ bPC        │ 0.0390209  │ 0.0972249 │ 0.000972249 │ 0.00890519 │

Quantiles

│ Row │ parameters │ 2.5%      │ 25.0%      │ 50.0%      │ 75.0%    │ 97.5%    │

In [36]:
############# Statistical Rethinking - Chapter 12 - Trolley model (m12.1),

################# Need to optimize, TOOO SLOW, 5 hours for 1000 samples ################

## import data
Trolley= CSV.read("Trolley.csv",
    missingstrings = ["nan", "NA", "na", ""])

n_obs = size(Trolley)[1]

response = Trolley[:response]
n_response = length(unique(response))

action = Trolley[:action]
intention = Trolley[:intention]
contact = Trolley[:contact]



# define model, function Logistic in StatsFuns package
@model trolley_model(response, action, intention, contact) = begin
    
    # prior for bA
    bA ~ Normal(0, 10)
    
    # prior for bI
    bI ~ Normal(0, 10)
    
    # prior for bC
    bC ~ Normal(0, 10)
    
    # prior for a, 6
    a = Array{Real}(undef, 6)
    a ~ [Normal(0, 10)]
    b = sort(a)
    
    
    #likelihood
    
    theta = (bA .* action) .+ (bC .* contact) .+ (bI .* intention)
    
    p = Array{Real}(undef, (n_obs,7))
    
        p[:,1] = logistic.(b[1] .- theta)
    
    
    for k in 2:6
            p[:,k] = logistic.(b[k] .- theta) - logistic.(b[k-1] .- theta)
    end
    
        p[:,7] = 1 .- p[:,1] .- p[:,2] .- p[:,3] .- p[:,4] .- p[:,5] .- p[:,6]
    
    for i in 1:n_obs
        response[i] ~ Categorical(p[i,:])
    end   


    
    end;

iterations = 100
ϵ = 0.1
τ = 10

######### work for NUTS sampler but not HMC, need to check condition for p
# start sampling, HMC sampler
#chain_trolley = sample(trolley_model(response, action, intention, contact), HMC(iterations, ϵ, τ))

## NUTS samples
#chain_trolley_NUTS = sample(trolley_model(response, action, intention, contact), NUTS(iterations, 0.65))

## Dynamic NUTS samples
chain_trolley_DynamicNUTS = sample(trolley_model(response, action, intention, contact), DynamicNUTS(iterations))

# trace plot
#p = MCMCChains.plot(chain_admit_NUTS)

MCMC, adapting ϵ (75 steps)
1.2 s/step ...done
MCMC, adapting ϵ (25 steps)
1.7 s/step ...done
MCMC, adapting ϵ (50 steps)
2.1 s/step ...done
MCMC, adapting ϵ (100 steps)
step 100 (of 100), 0.78 s/step
0.78 s/step ...done
MCMC, adapting ϵ (200 steps)
step 100 (of 200), 0.76 s/step
step 200 (of 200), 0.72 s/step
0.72 s/step ...done
MCMC, adapting ϵ (400 steps)
step 100 (of 400), 0.67 s/step
step 200 (of 400), 0.67 s/step
step 300 (of 400), 0.65 s/step
step 400 (of 400), 0.65 s/step
0.65 s/step ...done
MCMC, adapting ϵ (50 steps)
1.1 s/step ...done
MCMC (100 steps)
step 100 (of 100), 0.62 s/step
0.62 s/step ...done


Object of type Chains, with data of type 100×12×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:100
Thinning interval = 1
Chains            = 1
Samples per chain = 100
internals         = eval_num, lf_num, lp
parameters        = a[3], a[4], bC, a[5], a[6], bI, a[2], a[1], bA

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean      │ std       │ naive_se   │ mcse    │ ess     │
│     │ Symbol     │ Float64   │ Float64   │ Float64    │ Missing │ Any     │
├─────┼────────────┼───────────┼───────────┼────────────┼─────────┼─────────┤
│ 1   │ a[1]       │ -2.15128  │ 0.0357294 │ 0.00357294 │ missing │ 100.0   │
│ 2   │ a[2]       │ 1.02775   │ 0.0318139 │ 0.00318139 │ missing │ 100.0   │
│ 3   │ a[3]       │ -2.83509  │ 0.0409348 │ 0.00409348 │ missing │ 100.0   │
│ 4   │ a[4]       │ -0.547329 │ 0.0278461 │ 0.00278461 │ missing │ 96.3126 │
│ 5   │ a[5]       │ 0.122236  │ 0.0302065 │ 0.00302065 │

In [169]:
############# Statistical Rethinking - Chapter 12 - Zero Inflated model (m12.4),

############# NEED TO CREATE A CUSTOMIZED DISTRIBUTION ################
prob_drink = 0.2
rate_work = 1

n_obs = 365
drink = rand(Binomial(1, prob_drink), n_obs)

y = (1 .- drink) .* rand(Poisson(rate_work), n_obs)

# define model, function Logistic in StatsFuns package
@model zero_model(y) = begin
    
    # prior for al
    al ~ Normal(0, 10)
    
    # prior for ap
    ap ~ Normal(0, 1)
    
    log_lambda = exp(al)
    logit_p = logistic(ap)
    
    
    #likelihood
    
    for i in 1:n_obs
        y[i] ~ Poisson(log_lambda) - Poisson(log_lambda) * Binomial(1, logit_p)
    end   

    
    end;

iterations = 1000
ϵ = 0.1
τ = 10

######### work for NUTS sampler but not HMC, need to check condition for p
# start sampling, HMC sampler
#chain_trolley = sample(trolley_model(response, action, intention, contact), HMC(iterations, ϵ, τ))

## NUTS samples
chain_zero_NUTS = sample(zero_model(y), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_admit_NUTS)

MethodError: MethodError: no method matching *(::Poisson{Float64}, ::Binomial{Float64})
Closest candidates are:
  *(::Any, ::Any, !Matched::Any, !Matched::Any...) at operators.jl:502
  *(!Matched::DataValues.DataValue{T1}, ::T2) where {T1, T2} at /Users/nhungnguyen/.julia/packages/DataValues/IGQzW/src/scalar/operations.jl:66
  *(::T1, !Matched::DataValues.DataValue{T2}) where {T1, T2} at /Users/nhungnguyen/.julia/packages/DataValues/IGQzW/src/scalar/operations.jl:76
  ...

In [37]:
############# Statistical Rethinking - Chapter 13 - Reedfrogs model (m13.2),

## import data
reedfrogs = CSV.read("reedfrogs.csv",
    missingstrings = ["nan", "NA", "na", ""])

n_obs = size(reedfrogs)[1]
surv = reedfrogs[:surv]
density = reedfrogs[:density]

# define model, function Logistic in StatsFuns package
@model reedfrogs_model(surv, density) = begin
    
    # prior for sigma
    sigma ~ Exponential(1)
    
    # prior for a
    a ~ Normal(0, 1)
    
    # prior for a_tank
    a_tank = Array{Real}(undef, n_obs)
    a_tank ~ [Normal(a, sigma)]
   
    
    #likelihood
    
    for i in 1:n_obs
        surv[i] ~ BinomialLogit(density[i], a_tank[i])
    end   


    
    end;

iterations = 1000
ϵ = 0.1
τ = 10

######### work for NUTS sampler but not HMC, need to check condition for p
# start sampling, HMC sampler
#chain_reedfrogs = sample(reedfrogs_model(surv, density), HMC(iterations, ϵ, τ))

## NUTS samples
chain_reedfrogs_NUTS = sample(reedfrogs_model(surv, density), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_reedfrogs_NUTS)



┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.33476562500000007
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
┌ Info:  Adapted ϵ = 0.19875323108182055, std = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]; 500 iterations is used for adaption.
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/adapt/adapt.jl:90


[NUTS] Finished with
  Running time        = 79.97879211799999;
  #lf / sample        = 0.0;
  #evals / sample     = 0.001;
  pre-cond. metric    = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0,....


Object of type Chains, with data of type 1000×56×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:1000
Thinning interval = 1
Chains            = 1
Samples per chain = 1000
internals         = eval_num, lf_num, lp
parameters        = a_tank[25], a_tank[41], sigma, a_tank[18], a_tank[1], a_tank[27], a_tank[7], a_tank[15], a_tank[12], a_tank[6], a_tank[31], a_tank[26], a_tank[11], epsilon, a_tank[8], a_tank[43], a_tank[48], a_tank[10], a_tank[20], a_tank[45], a_tank[47], a_tank[21], a_tank[37], a_tank[39], a_tank[13], a_tank[9], a_tank[29], a_tank[38], a_tank[40], a_tank[34], a_tank[19], a_tank[2], a_tank[14], a_tank[36], a_tank[22], a_tank[5], a_tank[4], a_tank[23], a_tank[42], a_tank[35], a_tank[46], a_tank[32], a_tank[30], elapsed, a, a_tank[17], a_tank[24], a_tank[33], lf_eps, a_tank[44], a_tank[28], a_tank[3], a_tank[16]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean      │ std       │ 

In [362]:
############# Statistical Rethinking - Chapter 14 - Island Distance model (m14.7),

####### NEED TO FIX TYPE ERROR ###############

############ AVOID USING FOR LOOP CUZ MODEL CAN NOT KEEP TRACK OF THE OPERATION #######################

## import data
## function load from RData maxtrix
Dmat = RData.load("islandsDistMatrix.rda", convert=true)
Dmat = DataFrame(Dmat.vals[10])
rename!(Dmat, o => n for (o,n) = zip([:x1, :x2, :x3, :x4, :x5, :x6, :x7, :x8, :x9, :x10]
            ,[:Ml, :Ti, :SC, :Ya, :Fi, :Tr, :Ch, :Mn, :To, :Ha]))


Kline2= CSV.read("Kline2.csv",
    missingstrings = ["nan", "NA", "na", ""])

n_obs = size(Kline2)[1]
n_soc = 10
society = 1:n_soc

log_pop = log.(Kline2[:population])
log_pop =  convert(Array{Float64}, log_pop)
total_tools = Kline2[:total_tools]
total_tools = convert(Array{Float64}, total_tools)


# define model, function Logistic in StatsFuns package
@model distance_model(tools, log_pop, Dmat) = begin
    
    # prior for rho squared
    rhosq = tzeros(1)
    rhosq ~ Truncated(Cauchy(0, 1), 0, Inf)
    
    # prior for eta squared
    etasq = tzeros(1)
    etasq ~ Truncated(Cauchy(0, 1), 0, Inf)
    
    # prior for bp
    bp = tzeros(1)
    bp ~ Normal(0, 1)
    
    # prior for a
    a = tzeros(1)
    a ~ Normal(0, 10)
    
    
    K_empty = zeros()
    
    for i in 1:n_soc
        for j in 1:n_soc
            ind = iszero(Dmat[i,j]) * 0.01
            K = etasq * exp(-rhosq * (Dmat[i,j]^2)) + ind
            K_empty = vcat(K_empty, K)
        end
    end
    
    K_empty = reshape(K_empty[2:101], 10, 10)
    
    g = Array{Float64}(undef)
    mu = Array{Float64}(zeros(10))
    
    g ~ MvNormal(mu, K_empty)
    
    for i in 1:n_obs
        log_lambda = a + g[i] + bp * log_pop[i]
        lambda = exp(log_lambda)
        tools[i] ~ Poisson(lambda)
    end   

    end;

iterations = 1000
ϵ = 0.1
τ = 10

######### work for NUTS sampler but not HMC, need to check condition for p
# start sampling, HMC sampler
#chain_distance = sample(distance_model(total_tools, log_pop, Dmat), HMC(iterations, ϵ, τ))

## NUTS samples
#chain_distance_NUTS = sample(distance_model(total_tools, log_pop, Dmat), NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_distance_NUTS)

# DynamicNUTS samples
chain_distance_DynamicNUTS = sample(distance_model(total_tools, log_pop, Dmat), DynamicNUTS(iterations))

MCMC, adapting ϵ (75 steps)
0.57 s/step ...done
MCMC, adapting ϵ (25 steps)
0.99 s/step ...done
MCMC, adapting ϵ (50 steps)
0.44 s/step ...done
MCMC, adapting ϵ (100 steps)
step 100 (of 100), 0.27 s/step
0.27 s/step ...done
MCMC, adapting ϵ (200 steps)
step 100 (of 200), 0.24 s/step
step 200 (of 200), 0.22 s/step
0.22 s/step ...done
MCMC, adapting ϵ (400 steps)
step 100 (of 400), 0.13 s/step
step 200 (of 400), 0.12 s/step
step 300 (of 400), 0.11 s/step
step 400 (of 400), 0.1 s/step
0.1 s/step ...done
MCMC, adapting ϵ (50 steps)
0.14 s/step ...done
MCMC (1000 steps)
step 100 (of 1000), 0.1 s/step
step 200 (of 1000), 0.099 s/step
step 300 (of 1000), 0.1 s/step
step 400 (of 1000), 0.1 s/step
step 500 (of 1000), 0.1 s/step
step 600 (of 1000), 0.1 s/step
step 700 (of 1000), 0.1 s/step
step 800 (of 1000), 0.1 s/step
step 900 (of 1000), 0.1 s/step
step 1000 (of 1000), 0.1 s/step
0.1 s/step ...done


Object of type Chains, with data of type 1000×17×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:1000
Thinning interval = 1
Chains            = 1
Samples per chain = 1000
internals         = eval_num, lf_num, lp
parameters        = g[9], g[1], etasq, rhosq, a, g[7], g[6], g[4], g[10], bp, g[2], g[5], g[8], g[3]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean      │ std      │ naive_se  │ mcse       │ ess     │
│     │ Symbol     │ Float64   │ Float64  │ Float64   │ Float64    │ Any     │
├─────┼────────────┼───────────┼──────────┼───────────┼────────────┼─────────┤
│ 1   │ a          │ 1.24648   │ 1.19673  │ 0.0378438 │ 0.0356377  │ 753.317 │
│ 2   │ bp         │ 0.251404  │ 0.117842 │ 0.0037265 │ 0.00301656 │ 834.756 │
│ 3   │ etasq      │ 0.382025  │ 0.754459 │ 0.0238581 │ 0.0392305  │ 478.388 │
│ 4   │ g[1]       │ -0.251994 │ 0.452032 │ 0.0142945 │ 0.0164907  │ 449.835 │
│ 5   │ g[2] 

In [423]:
############ Car model from Causact package ###############

car = CSV.read("carModelDF.csv",
    missingstrings = ["nan", "NA", "na", ""])
getCard = car[:getCard]
carModel = recode(car[:carModel], "Toyota Corolla" => 1, "Subaru Outback" => 2, "Kia Forte" => 3, "Jeep Wrangler" => 4)

addprocs(4)
@everywhere using Turing, Random, DynamicHMC, LogDensityProblems
for i in procs()
    @fetch @spawnat i Random.seed!(rand(Int64))
end

# define model, 
@everywhere @model car_model(card,car) = begin    #MODEL
car_dim  = length(unique(car))   #DIM
theta  = Array{Float64}(undef,car_dim)
theta  ~ [Beta(2, 2)] #PRIOR

    for i in 1:length(card) 
 card[i] ~Bernoulli(theta[car[i]])
 end 
 end;   #LIKELIHOOD

iterations = 1000
ϵ = 0.1
τ = 10



## NUTS samples
#chain_car_NUTS = sample(car_model(getCard, carModel), NUTS(iterations, 0.65))

# start sampling, HMC sampler
#chain_car = sample(car_model(getCard, carModel), HMC(iterations, ϵ, τ))

# start sampling, DynamicNUTS sampler
#chain_car_dynamicNUTS = sample(car_model(getCard, carModel), DynamicNUTS(1000))
num_chains = 4
sampler = Turing.NUTS(100, 0.65)
model = car_model(getCard, carModel)
chain_car_NUTS = reduce(chainscat, pmap(x->sample(model,sampler),1:num_chains))


      From worker 37:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 37:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 37:	└ @ Base loading.jl:947
      From worker 36:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 36:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 36:	└ @ Base loading.jl:947
      From worker 35:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 35:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 35:	└ @ Base loading.jl:947
      From worker 34:	┌ Warning: Module Dis

┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Req

ErrorException: invalid redefinition of constant model

In [415]:
## OX MODEL - MISSING DATA, CAN NOT RECOVER THE TRUE PARAMETER
using Distributed
addprocs(4)
@everywhere using Turing, Random, DynamicHMC, LogDensityProblems

# Set the progress to false to avoid too many notifications.
@everywhere turnprogress(false)

# Set a different seed for each process.
for i in procs()
    @fetch @spawnat i Random.seed!(rand(Int64))
end

## The specified DAG corresponds to the following Julia code: 
s_missing = fill(missing, 21)       #DATA
s_obs = [1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1]          #DATA
tea_missing = [1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0, 1]   #DATA
tea_obs = [1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]          #DATA

@everywhere @model ox_model(s_missing,s_obs,tea_missing,tea_obs) = begin    #MODEL
sigma  = Array{Float64}(undef,1)
sigma  ~ Beta(2, 2) #PRIOR
p_u    = Array{Float64}(undef,1)
p_u    ~ Beta(2, 2) #PRIOR
p_s    = Array{Float64}(undef,1)
p_s    ~ Beta(2, 2) #PRIOR

    for i in 1:length(s_missing  ) 
 s_missing[i] ~Binomial(1, sigma)
 end 
             #LIKELIHOOD
for i in 1:length(s_obs      ) 
 s_obs[i] ~Binomial(1, sigma)
 end 
                 #LIKELIHOOD
pi_missing = s_missing .* p_s .+ (1 .- s_missing) .* p_u   #OPERATION
pi_obs     = s_obs .* p_s .+ (1 .- s_obs) .* p_u           #OPERATION

    for i in 1:length(tea_missing) 
 tea_missing[i] ~Binomial(1, pi_missing[i])
 end 
   #LIKELIHOOD

    for i in 1:length(tea_obs    ) 
 tea_obs[i] ~Binomial(1, pi_obs[i])
 end 
           #LIKELIHOOD
end;


## NUTS samples
num_chains = 4
sampler = Turing.NUTS(10, 0.65)
#sampler = HMC(4000, 0.01, 10)
#sampler = DynamicNUTS(1000)
model = ox_model(s_missing,s_obs,tea_missing,tea_obs)

#chain_ox_NUTS = sample(ox_model(s_missing,s_obs,tea_missing,tea_obs), NUTS(6000, 0.65))


# Run all samples.
chain_ox_NUTS = reduce(chainscat, pmap(x->sample(model,sampler),1:num_chains))

      From worker 26:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 26:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 26:	└ @ Base loading.jl:947
      From worker 29:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 29:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 29:	└ @ Base loading.jl:947
      From worker 28:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 28:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 28:	└ @ Base loading.jl:947
      From worker 27:	┌ Warning: Module Dis

┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Req

ErrorException: invalid redefinition of constant model

In [434]:
############# Statistical Rethinking - Chapter 12 - Trolley model (m12.5), with ordered predictor variables

###### OVER FLOW/ UNDER FLOW WITH CATEGORICAL DISTRIBUTION ###############

############ TOOOO SLOW ##############


## import data
Trolley= CSV.read("Trolley.csv",
    missingstrings = ["nan", "NA", "na", ""])

edu = Trolley[:edu]
new_edu = recode(edu, "Elementary School" => 1, "Middle School"  => 2, "Some High School" => 3, 
    "High School Graduate" => 4, "Some College" => 5, "Bachelor's Degree" => 6,
    "Master's Degree" => 7, "Graduate Degree" => 8)

n_obs = size(Trolley)[1]

response = Trolley[:response]
n_response = length(unique(response))

action = Trolley[:action]
intention = Trolley[:intention]
contact = Trolley[:contact]



# define model, function Logistic in StatsFuns package
@model trolley_2(response, action, intention, contact, new_edu) = begin
    
    # prior for delta, a vector of 7
    #delta = tzeros(1)
    
    delta ~ Dirichlet(ones(7)*2)
    
    delta_j = prepend!(delta, 0.0)
    
    # prior for bA
    bA = tzeros(1)
    bA ~ Normal(0, 1)
    
    # prior for bI
    bI = tzeros(1)
    bI ~ Normal(0, 1)
    
    # prior for bC
    bC = tzeros(1)
    bC ~ Normal(0, 1)
    
    # prior for bE
    bE = tzeros(1)
    bE ~ Normal(0, 1)
    
    # prior for a, 6
    a = tzeros(6)
    #a = Array{Float64}(undef, 6)
    a ~ [Normal(0, 1.5)]
    b = sort(a)

    
    for i in 1:n_obs
        
        sum_of_delta = 0
        last = new_edu[i]
        
        for j in 1:last
            sum_of_delta += delta_j[j]
        end
        
        theta = (bE * sum_of_delta) + (bA * action[i]) + (bC * contact[i]) .+ (bI * intention[i])
        
        p_1 = logistic(b[1] - theta)
        
        p_2 = logistic(b[2] - theta) - logistic(b[1] - theta)
        
        p_3 = logistic(b[3] - theta) - logistic(b[2] - theta)
        
        p_4 = logistic(b[4] - theta) - logistic(b[3] - theta)
        
        p_5 = logistic(b[5] - theta) - logistic(b[4] - theta)
        
        p_6 = logistic(b[6] - theta) - logistic(b[5] - theta)
        
        p_7 = 1 - logistic(b[6] - theta)
        
        response[i] ~ Categorical([p_1, p_2, p_3, p_4, p_5, p_6, p_7])
         
        end 
        
        
       
    end;

iterations = 100
ϵ = 0.1
τ = 10

######### work for NUTS sampler but not HMC, need to check condition for p
# start sampling, HMC sampler
#chain_trolley = sample(trolley_2(response, action, intention, contact, new_edu), HMC(iterations, ϵ, τ))

## NUTS samples
chain_trolley_NUTS = sample(trolley_2(response, action, intention, contact, new_edu), Turing.NUTS(iterations, 0.65))

## Dynamic NUTS samples
#chain_trolley_2_DynamicNUTS = sample(trolley_2(response, action, intention, contact, new_edu), DynamicNUTS(iterations))

# trace plot
#p = MCMCChains.plot(chain_trolley_NUTS)


┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packag

┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packag

┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packag

[HMC] Finished with
  Running time        = 302.89997051499995;
  Accept rate         = 0.01;
  #lf / sample        = 0.99;
  #evals / sample     = 0.01;
  pre-cond. metric    = [1.0].


┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:170
┌ Warning: Numerical error in gradients. Rejecting current proposal...
└ @ Turing.Core /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/core/ad.jl:169
┌ Warning: grad = Real[NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN]
└ @ Turing.Core /Users/nhungnguyen/.julia/packag

Object of type Chains, with data of type 100×23×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:100
Thinning interval = 1
Chains            = 1
Samples per chain = 100
internals         = eval_num, lf_num, lp
parameters        = elapsed, delta[7], a[3], delta[2], a[4], bC, delta[6], a[5], delta[4], delta[5], bE, a[1], bA, lf_eps, a[6], delta[1], bI, epsilon, a[2], delta[3]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 2 columns
│ Row │ parameters │ mean       │ std         │ naive_se    │ mcse    │
│     │ Symbol     │ Float64    │ Float64     │ Float64     │ Missing │
├─────┼────────────┼────────────┼─────────────┼─────────────┼─────────┤
│ 1   │ a[1]       │ 2.59098    │ 8.92653e-16 │ 8.92653e-17 │ missing │
│ 2   │ a[2]       │ 2.52782    │ 0.0         │ 0.0         │ missing │
│ 3   │ a[3]       │ 0.552258   │ 0.0         │ 0.0         │ missing │
│ 4   │ a[4]       │ 0.792329   │ 0.0         │ 0.0         │ missing │

In [424]:
using Distributed
addprocs(4)
@everywhere using Turing, Random


# Set a different seed for each process.
for i in procs()
    @fetch @spawnat i Random.seed!(rand(Int64))
end

# Define the model using @everywhere.
@everywhere @model gdemo(x) = begin
    s ~ InverseGamma(2,3)
    m ~ Normal(0, sqrt(s))
    for i in eachindex(x)
        x[i] ~ Normal(m, sqrt(s))
    end
end

# Sampling setup.
num_chains = 4
sampler = NUTS(1000, 0.65)
model = gdemo([1.2, 3.5]

# Run all samples.
chns = reduce(chainscat, pmap(x->sample(model,sampler),1:num_chains))

      From worker 38:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 38:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 38:	└ @ Base loading.jl:947
      From worker 40:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 40:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 40:	└ @ Base loading.jl:947
      From worker 41:	┌ Warning: Module Distributions with build ID 212876940731922 is missing from the cache.
      From worker 41:	│ This may mean Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] does not support precompilation but is imported by a module that does.
      From worker 41:	└ @ Base loading.jl:947
      From worker 39:	┌ Warning: Module Dis

┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Required dependency Distributions [31c24e10-a181-5473-b8eb-7969acd0382f] failed to load from a cache file.
└ @ Base loading.jl:969
┌ Warning: The call to compilecache failed to create a usable precompiled cache file for Turing [fce5fe82-541a-59a6-adf8-730c64b5f9a0]
│   exception = Req

UndefVarError: UndefVarError: NUTS not defined

In [430]:
############# Statistical Rethinking - Chapter 12 - UCBadmit model (m12.1), BetaBinomial
## import data
UCBadmit= CSV.read("UCBadmit.csv",
    missingstrings = ["nan", "NA", "na", ""])

n_obs = size(UCBadmit)[1]

admit = UCBadmit[:admit]

applications = UCBadmit[:applications]

gid = [UCBadmit[:gender][i] == "male" ? 1 : 2 for i = 1:n_obs]


# define model
@model admit_model_2(admit, applications, gid) = begin
    
    # prior for bm
    theta ~ Exponential(1)
    
    # prior for as, 2 a
    a = Array{Real}(undef, 2)
    a ~ [Normal(0, 1.5)]
    
    
    #likelihood
    
    for i in 1:n_obs
        logit_pbar = a[gid][i]
        pbar = logistic(logit_pbar)
        admit[i] ~ BetaBinomial(applications[i], pbar, theta)
    end
    end;

iterations = 1000
ϵ = 0.1
τ = 10

# start sampling, HMC sampler
#chain_admit = sample(admit_model(admit, applications, male_id, dept_id), HMC(iterations, ϵ, τ))

## NUTS samples
chain_admit_2_NUTS = sample(admit_model_2(admit, applications, gid), Turing.NUTS(iterations, 0.65))

# trace plot
#p = MCMCChains.plot(chain_admit_NUTS)

#chain_admit_2_DynamicsNUTS = sample(admit_model_2(admit, applications, gid), DynamicNUTS(iterations))

[NUTS] Finished with
  Running time        = 4.00629618;
  #lf / sample        = 0.0;
  #evals / sample     = 0.001;
  pre-cond. metric    = [1.0, 1.0, 1.0].


┌ Info: [Turing] looking for good initial eps...
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:247
┌ Info: [Turing] found initial ϵ: 0.3875
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/support/hmc_core.jl:239
┌ Info:  Adapted ϵ = 0.41053716490101716, std = [1.0, 1.0, 1.0]; 500 iterations is used for adaption.
└ @ Turing.Inference /Users/nhungnguyen/.julia/packages/Turing/RZOZ8/src/inference/adapt/adapt.jl:90


Object of type Chains, with data of type 1000×9×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:1000
Thinning interval = 1
Chains            = 1
Samples per chain = 1000
internals         = eval_num, lf_num, lp
parameters        = theta, epsilon, elapsed, a[2], lf_eps, a[1]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean      │ std      │ naive_se   │ mcse       │ ess     │
│     │ Symbol     │ Float64   │ Float64  │ Float64    │ Float64    │ Any     │
├─────┼────────────┼───────────┼──────────┼────────────┼────────────┼─────────┤
│ 1   │ a[1]       │ 1.19851   │ 1.03901  │ 0.0328563  │ 0.0407818  │ 336.879 │
│ 2   │ a[2]       │ 1.14061   │ 0.995687 │ 0.0314864  │ 0.0518895  │ 333.935 │
│ 3   │ elapsed    │ 0.0040063 │ 0.039862 │ 0.00126055 │ 0.00145173 │ 6.52961 │
│ 4   │ epsilon    │ 0.481711  │ 0.439297 │ 0.0138918  │ 0.0284026  │ 48.2793 │
│ 5   │ lf_eps     │ 0.481711  │ 0.439297 │ 

In [457]:
############# Statistical Rethinking - Chapter 15- Milk model (m15.3), Bayesian Imputation
## import data
milk = CSV.read("milk.csv",
    missingstrings = ["nan", "NA", "na", ""])


## function to scale variables
function center(y)
    return((y .- mean(filter(!ismissing, y))) ./ std(filter(!ismissing, y)))
    end

## Scale KCalories, Neo and Mass
K = center(milk[:kcal_per_g])
B = center(milk[:neocortex_perc] / 100)
M = center(log.(milk[:mass]))

missing_index= findall(ismissing, B)
non_missing_index = findall(!ismissing, B)

B_nm = B[non_missing_index]

K_nm = K[non_missing_index]
K_m = K[missing_index]

M_nm = M[non_missing_index]
M_m = M[missing_index]

# define model
@model milk15_3(K_nm, K_m, B_nm, M_nm, M_m) = begin
    
    #prior for sigma
    sigma ~ Exponential(1)
    
    #prior for sigma_B
    sigma_B ~ Exponential(1)
    
    # prior for bM
    bM ~ Normal(0, 0.5)
    
    # prior for bB
    bB ~ Normal(0, 0.5)
    
    # prior for intercept
    a ~ Normal(0, 0.5)
    
    # prior for nu
    nu ~ Normal(0, 0.5)
    
    # prior for B_m
    B_m = Array{Float64}(undef, 12)
    B_m ~ [Normal(nu, sigma_B)]
    
    #likelihood
    n_missing = length(K_m)
    n_non_missing = length(K_nm)
    
    for i in 1:n_missing
        mu_m = a + bB * B_m[i] + bM * M_m[i]
        K_m[i] ~ Normal(mu_m, sigma)
    end
    
    for j in 1:n_non_missing
        B_nm[j] ~ Normal(nu, sigma_B)
        mu_nm = a + bB * B_nm[j] + bM * M_nm[j]
        K_nm[j] ~ Normal(mu_nm, sigma)
    end
    
    end;

iterations = 1000
ϵ = 0.05
τ = 10

# start sampling
#chain_milk_15_3_NUTS = sample(milk15_3(K_nm, K_m, B_nm, M_nm, M_m), Turing.NUTS(iterations, 0.65))

chain_milk_15_3_DynamicNUTS = sample(milk15_3(K_nm, K_m, B_nm, M_nm, M_m), DynamicNUTS(iterations))


MCMC, adapting ϵ (75 steps)
0.033 s/step ...done
MCMC, adapting ϵ (25 steps)
0.037 s/step ...done
MCMC, adapting ϵ (50 steps)
0.027 s/step ...done
MCMC, adapting ϵ (100 steps)
step 100 (of 100), 0.016 s/step
0.016 s/step ...done
MCMC, adapting ϵ (200 steps)
step 100 (of 200), 0.013 s/step
0.011 s/step ...done
MCMC, adapting ϵ (400 steps)
step 113 (of 400), 0.0089 s/step
step 244 (of 400), 0.0082 s/step
step 386 (of 400), 0.0078 s/step
0.0078 s/step ...done
MCMC, adapting ϵ (50 steps)
0.0089 s/step ...done
MCMC (1000 steps)
step 149 (of 1000), 0.0067 s/step
step 291 (of 1000), 0.0069 s/step
step 427 (of 1000), 0.007 s/step
step 560 (of 1000), 0.0072 s/step
step 698 (of 1000), 0.0072 s/step
step 830 (of 1000), 0.0073 s/step
step 957 (of 1000), 0.0074 s/step
0.0073 s/step ...done


Object of type Chains, with data of type 1000×21×1 Array{Union{Missing, Float64},3}

Log evidence      = 0.0
Iterations        = 1:1000
Thinning interval = 1
Chains            = 1
Samples per chain = 1000
internals         = eval_num, lf_num, lp
parameters        = B_m[3], nu, B_m[1], B_m[10], B_m[5], B_m[7], B_m[6], B_m[8], a, sigma, B_m[2], bB, bM, sigma_B, B_m[4], B_m[11], B_m[12], B_m[9]

2-element Array{ChainDataFrame,1}

Summary Statistics
. Omitted printing of 1 columns
│ Row │ parameters │ mean       │ std      │ naive_se   │ mcse       │ ess     │
│     │ Symbol     │ Float64    │ Float64  │ Float64    │ Float64    │ Any     │
├─────┼────────────┼────────────┼──────────┼────────────┼────────────┼─────────┤
│ 1   │ B_m[1]     │ -0.603285  │ 0.921386 │ 0.0291368  │ 0.0376191  │ 1000.0  │
│ 2   │ B_m[2]     │ -0.674654  │ 0.902122 │ 0.0285276  │ 0.0245939  │ 1000.0  │
│ 3   │ B_m[3]     │ -0.722516  │ 0.916303 │ 0.028976   │ 0.0307034  │ 948.438 │
│ 4   │ B_m[4]     │ -0.330099  